# ANOMALY DETECTION ALGORITHM 

## From unsupervised to supervised learning

Let df denote a dataframe with two features; number of bets per minute and 200's. We first fit that data into a probability distribution. After that we detect the outliers and finally we replace the extreme values (like load tests, big events etc.) with an average value. This mitigates the noise of our data.  

In [ ]:
import numpy as np
import pandas as pd
import itertools
import logging
import warnings
import scipy.stats as st
import statsmodels as sm
import math
# import urllib3
from statistics import mean
from scipy.stats import *
from splunk_hec_handler import SplunkHecHandler
from datetime import datetime, timedelta

%matplotlib inline

df = pd.read_csv("sportsbook_NN_data_spare.csv")

# urllib3.disable_warnings()

# Create models from data

def best_fit_distribution(data, bins=200, ax=None):
    """Model data by finding best fit distribution to data"""
    # Get histogram of original data
    y, x = np.histogram(data, bins=bins, density=True)
    x = (x + np.roll(x, -1))[:-1] / 2.0

    # Distributions to check
    DISTRIBUTIONS = [        
        st.alpha,st.anglit,st.arcsine,st.beta,st.betaprime,st.bradford,st.burr,st.cauchy,st.chi,st.chi2,st.cosine,
        st.dgamma,st.dweibull,st.erlang,st.expon,st.exponnorm,st.exponweib,st.exponpow,st.f,st.fatiguelife,st.fisk,
        st.foldcauchy,st.foldnorm,st.genlogistic,st.genpareto,st.gennorm,st.genexpon,
        st.genextreme,st.gausshyper,st.gamma,st.gengamma,st.genhalflogistic,st.gilbrat,st.gompertz,st.gumbel_r,
        st.gumbel_l,st.halfcauchy,st.halflogistic
    ]


    # Best holders
    best_distribution = st.norm
    best_params = (0.0, 1.0)
    best_sse = np.inf

    
    list_s = []
    # Estimate distribution parameters from data
    for distribution in DISTRIBUTIONS:

        # Try to fit the distribution
        try:
            # Ignore warnings from data that can't be fit
            with warnings.catch_warnings():
                warnings.filterwarnings('ignore')

                # fit dist to data
                params = distribution.fit(data)

                # Separate parts of parameters
                arg = params[:-2]
                loc = params[-2]
                scale = params[-1]

                # Calculate fitted PDF and error with fit in distribution
                pdf = distribution.pdf(x, loc=loc, scale=scale, *arg)
                sse = np.sum(np.power(y - pdf, 2.0))

                # if axis pass in add to plot
                try:
                    if ax:
                        pd.Series(pdf, x).plot(ax=ax)
                    end
                except Exception:
                    pass

                # identify if this distribution is better
                if best_sse > sse > 0:
                    best_distribution = distribution
                    best_params = params
                    best_sse = sse

        except Exception:
            pass
        
        list_s.append((distribution.name,sse))

        z, w = zip(*list_s)
    
    data_frame = pd.DataFrame({'Dist': z, 'Error': w})
    print(data_frame.to_string())
    print("\n")
    print((list(z)[list(w).index(min(list(w)))],min(list(w))))
    print("\n")
    return (best_distribution.name, best_params)

def make_pdf(dist, params, size=10000):
    """Generate distributions's Probability Distribution Function """

    # Separate parts of parameters
    arg = params[:-2]
    loc = params[-2]
    scale = params[-1]

    # Get sane start and end points of distribution
    start = dist.ppf(0.01, *arg, loc=loc, scale=scale) if arg else dist.ppf(0.01, loc=loc, scale=scale)
    end = dist.ppf(0.99, *arg, loc=loc, scale=scale) if arg else dist.ppf(0.99, loc=loc, scale=scale)

    # Build PDF and turn into pandas Series
    x = np.linspace(start, end, size)
    y = dist.pdf(x, loc=loc, scale=scale, *arg)
    pdf = pd.Series(y, x)

    return pdf

# Load data from statsmodels datasets
data = pd.Series(df["NoB"]).iloc[-1440:]

# Find best fit distribution
best_fit_name, best_fit_params = best_fit_distribution(data, 200) 
best_dist = getattr(st, best_fit_name)

# Make PDF with best params 
pdf = make_pdf(best_dist, best_fit_params)

######################################################### Second Part ########################################################## 

# the code below disregards the ouliers in 200's; there are discrete cases where huge peaks appear (no-obvious reason) 
q = df["count_200"].quantile(0.90)

index_list_quantile = []

for j in range(len(df["count_200"])):
    if df["count_200"][j] >= int(q):
        index_list_quantile.append(j)

df["count_200"].replace(df["count_200"][index_list_quantile], df["count_200"].mean(), inplace=True)     

# we define our main frame with Sportsbook Web number of bets per minute over some period of Time (here is 4 months approx.)
main_df = df[["_time", "NoB"]]

Time_list = []
dist = best_dist

# takes the last day of the sample and creates a list with all minutes. 
# In principle we must be able to use epoch Time for constant data flow.
for i in main_df["_time"]:    
        Time_list.append(i)
        
# Time_ = map(lambda x : x.split(" ")[1], Time_list)
Time = Time_list 

#  we enumerate the Time-list so that we can exploit previous elements

listTime =[]

for i in range(len(Time)):
    listTime.append((Time[i],i))
    
#  we split the listTime in to distinct lists for later use; j_1 contains "%H:%M", j_2 contains  range(0,1441)
J_1, J_2 = zip(*listTime)
j_1 = list(J_1)
j_2 = list(J_2)

for i in range(len(j_1)):
    j_1[i] = j_1[i].split()[3]
    
j_1 = j_1[:1440] 

def series(j):
    return list(main_df[main_df["_time"].str.contains(j)]["NoB"])

def fun_200(j):
    return list(df[df["_time"].str.contains(j)]["count_200"].apply(lambda x : int(x)))

def time(j):       
    return list(main_df[main_df["_time"].str.contains(j)]["_time"])

def perc(mean,y):    
    return (100*(y-mean))/mean

list_character=[]
list_char=[]
list_1=[]
list_2=[]
list_3=[]

for j in range(len(j_1)):
    
    mean_j = mean(series(j_1[j])[:-1])
    list_1.append(series(j_1[j])[-1])
    list_2.append(fun_200(j_1[j])[-1])
    list_3.append(time(j_1[j])[-1])
    
    if (perc(mean_j, series(j_1[j])[-1]) <= -20): 
    
        if (max(series(j_1[j])) < best_dist.interval(0.95, *best_fit_params)[1]): 
        
           if (perc(mean_j, series(j_1[j])[-1]) <= -70) & (perc(mean(series(j_1[j-1])), series(j_1[j-1])[-1]) <= -70) & (perc(mean(series(j_1[j-2])), series(j_1[j-2])[-1]) <= -70):
                x1 = "High risk. The percentage drop is lower than {}% for more than 3 minutes.".format(j_1[j])
                list_char.append(x1)
                print(x_1)
           
        
           elif (perc(mean(fun_200(j_1[j])[:-1]),fun_200(j_1[j])[-1]) < -20): 
                x2 = "There is a {} % drop at {} o'clock and {} drop at 200's".format(math.ceil(perc(mean_j,series(j_1[j])[-1])),j_1[j],math.ceil(perc(mean(fun_200(j_1[j])[:-1]),fun_200(j_1[j])[-1])))
                list_char.append(x2)
                print(x2)
     
           else:
                print("{} We have a normal decrease.".format(j_1[j])) 
        else:
            if ((max(series(j_1[j-1])) > best_dist.interval(0.95, *best_fit_params)[1]) |
                (max(series(j_1[j-2])) > best_dist.interval(0.95, *best_fit_params)[1])):
                x3 = "{} Low Risk".format(j_1[j])
                list_char.append(x3)
                print(x3)
        
    else:        
        x4 = "{} No problem with the channel".format(j_1[j])
        list_char.append(x4)
        print(x4)
    
    if 'drop' in list_char[-1]:
        list_character.append(1)
    else:
        list_character.append(0)
        
df_ = pd.DataFrame({'_time':list_3, 'NoB':list_1, '200':list_2})
df_train = pd.concat([df_.reset_index(drop=True),pd.DataFrame({'Characters':list_character}).reset_index(drop=True)], axis=1)

df_train.to_csv('NN_training_data.csv', sep=',')    

# Anomaly detection - Neural Network.

The first attempt is to use a simple logistic regression model;
although it performs (unexpectedly) well, regression cannot self-learn. 
Therefore we move to more complex solutions.

In [2]:
import pandas as pd
import numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix
from imblearn.over_sampling import SMOTE

df = pd.read_csv("NN_training_data.csv")
del df["Unnamed: 0"]
del df["_time"]

X = df[["NoB","200"]]
y = df["Target"]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25)

smt = SMOTE()
X_train, y_train = smt.fit_sample(X_train, y_train)

log_reg = LogisticRegression()
log_reg.fit(X_train, y_train)
predictions=log_reg.predict(X_test)
print(log_reg.score(X,y))
print("\n")
print(classification_report(y_test,predictions))
print("\n")
print(confusion_matrix(y_test,predictions))

Using TensorFlow backend.


0.7993055555555556


              precision    recall  f1-score   support

           0       0.99      0.80      0.88       654
           1       0.31      0.92      0.47        66

   micro avg       0.81      0.81      0.81       720
   macro avg       0.65      0.86      0.67       720
weighted avg       0.93      0.81      0.84       720



[[520 134]
 [  5  61]]


C:\Users\dtomlinson\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:433: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


We implement the MLPClassifier from scikit-learn. 
This is the neural network analogue of tensorflow in sklearn.
It doesn't have the same functionality, thus if we don't hit 
a high score we won't use it further alone. 

We implement other libraries from the sklearn deep learning toolkit. 
In the cell below we use also Stohastic Gradient Descent and Gradient 
Boosting classifier.

In [67]:
import pandas as pd
import numpy as np
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.linear_model import SGDClassifier

df = pd.read_csv("NN_training_data.csv")
del df["Unnamed: 0"]
del df["_time"]

X = df[["NoB","200"]]
y = df["Target"]

from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
# Fit only to the training data
scaler.fit(X_train)

# Now apply the transformations to the data:
X_train = scaler.transform(X_train)
X_test = scaler.transform(X_test)

from sklearn.neural_network import MLPClassifier
from imblearn.over_sampling import SMOTE

mlp = MLPClassifier(hidden_layer_sizes=(5,5), activation="relu")

mlp.fit(X_train,y_train)

predictions = mlp.predict(X_test)

print(mlp.score(X,y))
print("\n")
print(confusion_matrix(y_test,predictions))
print("\n")
print(classification_report(y_test,predictions))

# mlp.coefs_
# mlp.intercepts_

model = GradientBoostingClassifier()
model.fit(X_train, y_train)
model.predict(X_test)

print(model.score(X,y))
print("\n")


stohastic_model = SGDClassifier(loss="hinge", penalty="l2", max_iter=5)
stohastic_model.fit(X_train, y_train)
stohastic_model.predict(X_test)

print(stohastic_model.score(X,y))

# print(confusion_matrix(y_test,predictions))
# print("\n")
# print(classification_report(y_test,predictions))

0.6763888888888889


[[223  22]
 [ 10 105]]


              precision    recall  f1-score   support

           0       0.96      0.91      0.93       245
           1       0.83      0.91      0.87       115

   micro avg       0.91      0.91      0.91       360
   macro avg       0.89      0.91      0.90       360
weighted avg       0.92      0.91      0.91       360

0.6763888888888889


0.6763888888888889


# Neural Network - Keras/Pandas/Numpy

The first cell contains the baseline of the neural network. We 
only feed a neural network of sixty-neurons in the hidden leayer 
to check the accuracy generically. The second cell consists a 
Standardized version of the first. There is no other difference. 
Nevertheless with that small change we hit a better result (thus 
we keep that change). 

The third cell computationally is more efficient than the other 
two; we use a thirty-layer neural network (reduce it by half) and 
the width of the neural network smaller.

In [44]:
import numpy as np
import pandas as pd
import warnings
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

warnings.filterwarnings("ignore")

seed = 7
numpy.random.seed(seed)

df = pd.read_csv("NN_training_data.csv")

del df["Unnamed: 0"]
del df["_time"]

dataset = df.values

X = df[["NoB","200"]]
y = df["Target"]

# baseline model
def create_baseline():
# create model
    model = Sequential()
    model.add(Dense(60, input_dim=2, kernel_initializer='normal', activation='relu'))
    model.add(Dense(1, kernel_initializer='normal', activation='sigmoid'))
# Compile model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

# evaluate model with standardized dataset
estimator = KerasClassifier(build_fn=create_baseline, epochs=100, batch_size=5, verbose=0)
kfold = StratifiedKFold(n_splits=10, shuffle=True, random_state=seed)
results = cross_val_score(estimator, X, y, cv=kfold)
print("Results: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Results: 69.36% (21.95%)


In [53]:
import numpy as np
import pandas as pd
import warnings
from keras.models import Sequential
from keras.layers import Dense
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

warnings.filterwarnings("ignore")

seed = 7
numpy.random.seed(seed)

df = pd.read_csv("NN_training_data.csv")

del df["Unnamed: 0"]
del df["_time"]

dataset = df.values

X = df[["NoB","200"]]
y = df["Target"]

estimators = []
estimators.append(('standardize', StandardScaler()))
estimators.append(('mlp', KerasClassifier(build_fn=create_baseline, epochs=100, batch_size=5, verbose=0)))
pipeline = Pipeline(estimators)
kfold = StratifiedKFold(n_splits=10, shuffle=True, random_state=seed)
results = cross_val_score(pipeline, X, y, cv=kfold)
print("Standardized: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))

Standardized: 91.11% (3.06%)


This is the most efficient NN we constructed so far. It's not "very" deep; fact that reflects the low complexity of our data. Nevertheless it takes ~5 minutes (when n_splits of cross_val_score has been set to 10) to evaluate the mean precision of the model.

In [1]:
import numpy
import pandas as pd
import warnings
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.optimizers import SGD
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score, cross_val_predict
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import StratifiedKFold
from sklearn.pipeline import Pipeline
from sklearn.metrics import confusion_matrix
from keras import regularizers

warnings.filterwarnings("ignore")

seed = 7
numpy.random.seed(seed)

df = pd.read_csv("NN_training_data.csv")

del df["Unnamed: 0"]
del df["_time"]

dataset = df.values

X = df[["NoB","200"]]
y = df["Target"]

# smaller model
def optimal_nn():
# create model
    model = Sequential()
    model.add(Dense(5, input_dim=2, kernel_initializer='normal', activation='relu', kernel_regularizer=regularizers.l2(0.001)))
    model.add(Dense(5, activation='relu', kernel_regularizer=regularizers.l2(0.001)))
    model.add(Dense(5, activation='relu', kernel_regularizer=regularizers.l2(0.001)))
    model.add(Dense(1, activation='sigmoid', kernel_regularizer=regularizers.l2(0.001)))
# Compile model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model
 
estimators = []
estimators.append(('standardize', StandardScaler()))
estimators.append(('mlp', KerasClassifier(build_fn=optimal_nn, epochs=50, batch_size=5, verbose=0)))
pipeline = Pipeline(estimators)
kfold = StratifiedKFold(n_splits=2, shuffle=True, random_state=seed)
results = cross_val_score(pipeline, X, y, cv=kfold)



#  CAUTION: the y_pred here does not necessarily return the same predictions with the results above. 
#  Generally, cross_val_score and cross_predict form two different scikit_learn functions, therefore
#  obey their own rules; their difference is mainly how the data is split in batches.
#  Nevertheless, it forms an approximation of the cross_val_score. Remember, cross_val_predict fits
#  each data sample EXACTLY ONCE in a test set and the confusion_matrix returns the prediction for this 
#  data sample that given time (hence explains why we have: len(y_pred)=len(y)=1440). 

y_pred = cross_val_predict(pipeline, X, y, cv=kfold)
conf_mat = confusion_matrix(y, y_pred)
print("Smaller Standardized NN: %.2f%% (%.2f%%)" % (results.mean()*100, results.std()*100))
print(conf_mat)

Using TensorFlow backend.


Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Use tf.cast instead.
Smaller Standardized NN: 91.11% (0.27%)
[[2597    0]
 [ 245   38]]


VERY Interesting fact : Without using the StandardScaler() function our model is really poor. In particular, it hits 63% percent without the StandardScaler() and furthermore it doesn't recognize the y-values equal to 1 (i.e., when there is a problem); in other words it's not working. Below the first cell contains the non-standardized version and the second when StandardScaler() is considered. Also we provide a classification report for comparison. 

In [65]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

mlp = KerasClassifier(build_fn=optimal_nn, epochs=100, batch_size=5, verbose=0)

X_train, X_test, y_train, y_test = train_test_split(X,y,test_size=0.25)
mlp.fit(X_train,y_train)

predictions = mlp.predict(X_test)

print(classification_report(y_test,predictions))

              precision    recall  f1-score   support

           0       0.63      1.00      0.77       227
           1       0.00      0.00      0.00       133

   micro avg       0.63      0.63      0.63       360
   macro avg       0.32      0.50      0.39       360
weighted avg       0.40      0.63      0.49       360



In [21]:
import numpy as np
import pandas as pd
import warnings
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.optimizers import SGD
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score, cross_val_predict
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import StratifiedKFold
from sklearn.pipeline import Pipeline
from sklearn.metrics import confusion_matrix
from keras import regularizers
from imblearn.over_sampling import SMOTE

df = pd.read_csv("NN_training_data.csv")

del df["Unnamed: 0"]
del df["_time"]

dataset = df.values

X = df[["NoB","200"]]
y = df["Target"]

mlp = KerasClassifier(build_fn=optimal_nn, epochs=100, batch_size=5, verbose=0)

from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X,y,test_size=0.25)

smt=SMOTE()
X_train, y_train = smt.fit_sample(X_train,y_train)
np.bincount(y_train)

scaler = StandardScaler()
# Fit only to the training data
scaler.fit(X_train)

# Now apply the transformations to the data:
X_train = scaler.transform(X_train)
X_test = scaler.transform(X_test)

mlp.fit(X_train,y_train)
predictions = mlp.predict(X_test)

from sklearn.metrics import classification_report, confusion_matrix
print(classification_report(y_test,predictions))
print("\n")
print(confusion_matrix(y_test,predictions))

mlp.save("mlp_classifier.model")

              precision    recall  f1-score   support

           0       0.99      0.77      0.87       640
           1       0.35      0.96      0.51        80

   micro avg       0.79      0.79      0.79       720
   macro avg       0.67      0.87      0.69       720
weighted avg       0.92      0.79      0.83       720



[[495 145]
 [  3  77]]


AttributeError: 'KerasClassifier' object has no attribute 'save'

In [18]:
import numpy
import pandas as pd
import warnings
from keras.models import Sequential
from keras.layers import Dense, Dropout
from keras.optimizers import SGD
from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from keras import regularizers
from keras.callbacks import EarlyStopping, ModelCheckpoint
import tensorflow as tf

warnings.filterwarnings("ignore")

seed = 7
numpy.random.seed(seed)

df = pd.read_csv("NN_training_data.csv")

del df["Unnamed: 0"]
del df["_time"]

dataset = df.values

X = df[["NoB","200"]]
y = df["Target"]

# Sequential
model = Sequential()

# Neural network
model.add(Dense(5, input_dim=2, kernel_initializer='normal', activation='tanh', kernel_regularizer=regularizers.l2(0.001)))
# model.add(Dropout(0.2))
model.add(Dense(1, activation='sigmoid', kernel_regularizer=regularizers.l2(0.001)))


# Compile model
# sgd = optimizers.SGD(lr=0.01, decay=0.0, momentum=0.0, nesterov=False)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

# callback=tf.keras.callbacks.EarlyStopping(monitor='val_acc', patience=10)

# Fit model
history = model.fit(X, y, epochs=5, validation_split=0.2, batch_size=5)

# tf.keras.callbacks.ModelCheckpoint('NN_anomaly_alter.model', monitor='val_acc', verbose=0, save_best_only=False, save_weights_only=False, mode='auto', period=1)

print(model.get_weights())

model.save('NN_anomaly_1.model')

Train on 2304 samples, validate on 576 samples
Epoch 1/5
2304/2304 [==============================] - 2s 822us/step - loss: 0.3760 - acc: 0.8772 - val_loss: 0.1549 - val_acc: 1.0000
Epoch 2/5
2304/2304 [==============================] - 1s 282us/step - loss: 0.3749 - acc: 0.8772 - val_loss: 0.1309 - val_acc: 1.0000
Epoch 3/5
2304/2304 [==============================] - 1s 295us/step - loss: 0.3744 - acc: 0.8772 - val_loss: 0.1326 - val_acc: 1.0000
Epoch 4/5
2304/2304 [==============================] - 1s 283us/step - loss: 0.3745 - acc: 0.8772 - val_loss: 0.1337 - val_acc: 1.0000
Epoch 5/5
2304/2304 [==============================] - 1s 282us/step - loss: 0.3744 - acc: 0.8772 - val_loss: 0.1336 - val_acc: 1.0000
[array([[-2.9095856e-03, -2.1770846e-03, -1.9934693e-16,  5.5312752e-03,
         1.8497715e-02],
       [ 4.6612010e-03,  7.4044587e-03, -8.8255713e-03,  1.1704177e-02,
         1.3716479e-02]], dtype=float32), array([ 0.00893806,  0.00683938, -0.01635896,  0.00989568,  0.0133

In [71]:
import tensorflow as tf
model1 = tf.keras.models.load_model("NN_anomaly_nice.model")
# model2 = tf.keras.models.load_model("NN_anomaly_nice.model")
# model3 = tf.keras.models.load_model("NN_anomaly.model")
X=pd.read_csv("01.09.2019_NN_test_data.csv")


In [72]:
prediction1=model1.predict(X)
# prediction2=model2.predict(X1)
# prediction3=model3.predict(X1)

In [73]:
list_1=[]
for i in range(len(prediction1)):
    if prediction1[i][0] > 0.5:
        list_1.append(i)

In [19]:
df = pd.read_csv("NN_training_data.csv")

In [20]:
df.head()

Unnamed: 0             _time  NoB   200  logins  Target
0         0.0  Fri Jul 12 00:00  149  3391     697       0
1         1.0  Fri Jul 12 00:01  129  3854     782       0
2         2.0  Fri Jul 12 00:02  114  3160     761       0
3         3.0  Fri Jul 12 00:03   95  3485     792       0
4         4.0  Fri Jul 12 00:04   28  3136     739       0